In [2]:
import pandas as pd

content = pd.read_json('content.jsonl', lines=True)
rating = pd.read_json('ratings.jsonl', lines=True)
targets = pd.read_csv('targets.csv')



In [3]:
genres = content[['ItemId', 'Genre']]
rating = pd.merge(rating, genres, on='ItemId', how='left')
rating.head()

UserId      ItemId           Timestamp  Rating   
0  c4ca4238a0  91766eac45 2013-10-05 22:00:50       8  \
1  c81e728d9d  5c739554f7 2013-08-17 16:26:38       9   
2  c81e728d9d  48f6d7ce7c 2013-08-17 13:28:27       8   
3  c81e728d9d  e9318d627a 2013-06-15 15:38:09       1   
4  a87ff679a2  17e6357973 2014-01-31 23:27:59       8   

                          Genre  
0        Action, Horror, Sci-Fi  
1    Action, Adventure, Fantasy  
2  Animation, Action, Adventure  
3       Action, Fantasy, Horror  
4              Biography, Drama

In [64]:
#if the user has ratings lower than 6, we will consider it as a negative rating, otherwise, it will be considered as a positive rating.

rating['Rating_type'] = rating['Rating'].apply(lambda x: 'Negative' if x < 6 else 'Positive')
rating.head()



UserId      ItemId           Timestamp  Rating   
0  c4ca4238a0  91766eac45 2013-10-05 22:00:50       8  \
1  c81e728d9d  5c739554f7 2013-08-17 16:26:38       9   
2  c81e728d9d  48f6d7ce7c 2013-08-17 13:28:27       8   
3  c81e728d9d  e9318d627a 2013-06-15 15:38:09       1   
4  a87ff679a2  17e6357973 2014-01-31 23:27:59       8   

                          Genre Rating_type  
0        Action, Horror, Sci-Fi    Positive  
1    Action, Adventure, Fantasy    Positive  
2  Animation, Action, Adventure    Positive  
3       Action, Fantasy, Horror    Negative  
4              Biography, Drama    Positive

In [65]:

# create a dictionary of the users positive ratings genres and another one for the negative ratings genres.
positive_genres_by_user = rating[rating['Rating'] >= 6].groupby('UserId')['Genre'].apply(lambda x: list(set(x))).to_dict()
negative_genres_by_user = rating[rating['Rating'] < 6].groupby('UserId')['Genre'].apply(lambda x: list(set(x))).to_dict()

def process_genres(genres_dict):
    processed_dict = {}
    for user, genres_list in genres_dict.items():
        # Dividir cada string por vírgula e espaço, e remover espaços extras
        split_genres = [genre.strip() for genres in genres_list for genre in genres.split(',')]
        # Remover duplicatas
        unique_genres = list(set(split_genres))
        processed_dict[user] = unique_genres
    return processed_dict

# Processar os dicionários de gêneros positivos e negativos
processed_positive_genres_by_user = process_genres(positive_genres_by_user)
processed_negative_genres_by_user = process_genres(negative_genres_by_user)


for user in processed_positive_genres_by_user:
    if user in processed_negative_genres_by_user:
        print(f"User {user}: Positive genres - {processed_positive_genres_by_user[user]}, Negative genres - {processed_negative_genres_by_user[user]}")
    else:
        print(f"User {user}: Positive genres - {processed_positive_genres_by_user[user]}, Negative genres - []")
        
for user in processed_negative_genres_by_user:
    if user not in processed_positive_genres_by_user:
        print(f"User {user}: Positive genres - [], Negative genres - {processed_negative_genres_by_user[user]}")


User 0004d0b59e: Positive genres - ['Biography', 'Drama', 'Action'], Negative genres - []
User 00053f5e11: Positive genres - ['Crime', 'Thriller', 'Mystery'], Negative genres - []
User 00056c20eb: Positive genres - ['Western', 'Adventure', 'Action'], Negative genres - []
User 0006246bee: Positive genres - ['Fantasy', 'Adventure', 'Sci-Fi', 'Action', 'Horror', 'Mystery', 'Thriller', 'Documentary', 'Crime', 'History', 'Western', 'Animation', 'Drama', 'Romance', 'Family', 'Biography', 'Comedy'], Negative genres - ['Adventure', 'Sci-Fi', 'Action', 'Horror', 'Thriller', 'Mystery', 'Crime', 'History', 'Sport', 'Drama', 'Romance', 'Fantasy', 'Comedy']
User 0006aabe0b: Positive genres - ['Sci-Fi', 'Adventure', 'Action'], Negative genres - []
User 0006dd05ea: Positive genres - ['Fantasy', 'Drama', 'Thriller'], Negative genres - []
User 0007789b11: Positive genres - ['Adventure', 'Sci-Fi', 'Action', 'Thriller', 'Crime', 'History', 'Animation', 'Drama', 'Romance', 'Comedy'], Negative genres - ['A

In [66]:
#for the movies from the positive rating column, create a dict with the user as key and the actors from the movies as values.

actors = content[['ItemId', 'Actors']]

rating = pd.merge(rating, actors, on='ItemId', how='left')

# Filtrar as avaliações positivas
positive_ratings = rating[rating['Rating_type'] == 'Positive']

# Fazer o merge com o DataFrame 'actors' para obter os atores dos filmes com avaliações positivas
positive_ratings_with_actors = pd.merge(positive_ratings, actors, on='ItemId', how='left')

# Função para converter a string de atores em uma lista
def split_actors(actors_str):
    return [actor.strip() for actor in actors_str.split(',') if actor]

# Aplicar a função para cada linha da coluna 'Actors'
positive_ratings_with_actors['Actors'] = positive_ratings_with_actors['Actors'].apply(split_actors)

# Criar um dicionário com o usuário como chave e os atores como valores
# Aqui utilizamos set para remover duplicatas e depois convertemos de volta para lista
positive_actors_by_user = positive_ratings_with_actors.groupby('UserId')['Actors'].apply(lambda x: list(set(actor for sublist in x for actor in sublist))).to_dict()

# Agora você tem um dicionário 'positive_actors_by_user' com os usuários e os atores únicos dos filmes avaliados positivamente

for user in positive_actors_by_user:
    print(f"User {user}: {positive_actors_by_user[user]}")

KeyError: 'Actors'

In [ ]:

user_movies_dict = targets.groupby('UserId')['ItemId'].apply(list).to_dict()

genres = content[['ItemId', 'Genre']]
actors = content[['ItemId', 'Actors']]

targets = pd.merge(targets, genres, on='ItemId', how='left')
targets = pd.merge(targets, actors, on='ItemId', how='left')
targets.head()

for user in user_movies_dict:
    




SyntaxError: incomplete input (83449626.py, line 13)

In [69]:
user_movies_dict = targets.groupby('UserId')['ItemId'].apply(list).to_dict()

genres = content[['ItemId', 'Genre']]
actors = content[['ItemId', 'Actors']]

targets = pd.merge(targets, genres, on='ItemId', how='left')
targets = pd.merge(targets, actors, on='ItemId', how='left')
targets.head()


#unique users in the targets dataset
targets_users = targets['UserId'].unique()

with open('submission.csv', 'w') as f:
    f.write('UserId,ItemId\n')

count = 0

for user in targets_users:

    relevance_list = []

    checkerG = False
    checkerA = False

    # get positive genres from the user
    if user in processed_positive_genres_by_user:
        positive_genres = processed_positive_genres_by_user[user]
        checkerG = True

   
    # get positive actors from the user
    if user in positive_actors_by_user:
        positive_actors = positive_actors_by_user[user]
        checkerA = True


    # get the movies from the user
    user_movies = user_movies_dict[user]

    # for each movie, check if it has a positive genre or actor
    if checkerG == True or checkerA == True:
        for movie in user_movies:
            
            # Get the movie genres, ensure it is a string and split by comma into a list
            if checkerG == True:
                movie_genre = targets[targets['ItemId'] == movie]['Genre'].values[0]
                if isinstance(movie_genre, str):
                    movie_genres_list = movie_genre.split(', ')
                else:
                    movie_genres_list = []
                
            

            # Get the movie actors, ensure it is a string and split by comma into a list
            if checkerA == True:
                movie_actors = targets[targets['ItemId'] == movie]['Actors'].values[0]
                if isinstance(movie_actors, str):
                    movie_actors_list = movie_actors.split(', ')
                else:
                    movie_actors_list = []

            checker = False

            if checkerG == True:
                for genre in movie_genres_list:
                    if genre in positive_genres:
                        relevance_list.insert(0, movie)
                        checker = True
                        break
                    
            if checkerA == True and checker == False:
                for actor in movie_actors_list:
                    if actor in positive_actors:
                        relevance_list.insert(0, movie)
                        checker = True
                        break

            if checker == False:           
                relevance_list.append(movie)
    else:
        relevance_list = user_movies
    #write the relevance list in the submission file, as userid,itemid
    with open('submission.csv', 'a') as f:
        for movie in relevance_list:
            f.write(f"{user},{movie}\n")
    count += 1
    print(count)
    

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [ ]:
user_movies_dict = targets.groupby('UserId')['ItemId'].apply(list).to_dict()

genres = content[['ItemId', 'Genre']]
actors = content[['ItemId', 'Actors']]

targets = pd.merge(targets, genres, on='ItemId', how='left')
targets = pd.merge(targets, actors, on='ItemId', how='left')
targets.head()


#unique users in the targets dataset
targets_users = targets['UserId'].unique()

with open('submission.csv', 'w') as f:
    f.write('UserId,ItemId\n')

for user in targets_users:
    relevance_list = []

    checkerG = False
    checkerA = False

    # get positive genres from the user
    if user in processed_positive_genres_by_user:
        positive_genres = processed_positive_genres_by_user[user]
        checkerG = True

   
    # get positive actors from the user
    if user in positive_actors_by_user:
        positive_actors = positive_actors_by_user[user]
        checkerA = True


    # get the movies from the user
    user_movies = user_movies_dict[user]

    # for each movie, check if it has a positive genre or actor
    if checkerG == True:
        
        for movie in user_movies:
            
            # Get the movie genres, ensure it is a string and split by comma into a list
            if checkerG == True:
                movie_genre = targets[targets['ItemId'] == movie]['Genre'].values[0]
                if isinstance(movie_genre, str):
                    movie_genres_list = movie_genre.split(', ')
                else:
                    movie_genres_list = []
                
            

            # Get the movie actors, ensure it is a string and split by comma into a list
            movie_actors = targets[targets['ItemId'] == movie]['Actors'].values[0]
            if isinstance(movie_actors, str):
                movie_actors_list = movie_actors.split(', ')
            else:
                movie_actors_list = []

            checker = False

            if checkerG == True:
                for genre in movie_genres_list:
                    if genre in positive_genres:
                        relevance_list.insert(0, movie)
                        checker = True
                        break
                    
            if checkerA == True and checker == False:
            if checker == False:
                for actor in movie_actors_list:
                    if actor in positive_actors:
                        relevance_list.insert(0, movie)
                        checker = True
                        break

            if checker == False:           
                relevance_list.append(movie)
    else:
        relevance_list = user_movies
    #write the relevance list in the submission file, as userid,itemid
    with open('submission.csv', 'a') as f:
        for movie in relevance_list:
            f.write(f"{user},{movie}\n")
    print(len(relevance_list))
    

In [ ]:
# put a header on submission.csv


